# HMC in 2D with variable mass matrix

This is a slightly more advanced version of HMC where the mass matrix can be set in the input parameters. The rest is similar to the case where the mass matrix equals the unit matrix.

**copyright**: Andreas Fichtner (andreas.fichtner@erdw.ethz.ch), December 2020

**license**: BSD 3-Clause (\"BSD New\" or \"BSD Simplified\")

## 0. Import Python packages

We begin with the import of a couple of Python packages, for plotting and for the 2D test functions that we will use. 

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import test_functions as f
from importlib import reload

plt.rcParams["font.family"] = "Times"
plt.rcParams.update({'font.size': 50})
plt.rcParams['xtick.major.pad']='12'
plt.rcParams['ytick.major.pad']='12'

## 1. Input parameters

Next, we set the basic input parameters, such as the total number of samples, the number of leap-frog iterations, the leap-frog integration timestep, and the kind of probability densities, expressed in terms of their associated potential energy $U$. Currently implemented potential energies are the following:

\begin{equation}
U(x,y) = (1.0-x)^2 + 100.0 *(y-x^2)^2\,,\qquad \text{(Rosenbrock function)}\,,
\end{equation}

\begin{equation}
U(x,y) = x^2 + y^2 + xy\,,\qquad \text{(quadratic function)}\,,
\end{equation}

\begin{equation}
U(x,y) = (x^2 + y - 11.0)^2 + (x + y^2 - 7.0)^2\,,\qquad \text{(Himmelblau function)}\,,
\end{equation}

\begin{equation}
U(x,y) = (x-2.0)^4 + (x - 2.0y)^2\,,\qquad \text{(Bazaraa-Shetty function)}\,.
\end{equation}

The input parameters are defined via the custom Python function input_parameters.py in order to be able to save a set of input parameters.

In [ ]:
import input_parameters
reload(input_parameters)
function,Minv,N,Nit,dt,plot_trajectories,autotune=input_parameters.input_parameters()

## 2. Plot test function

In the next step, we visualise the potential energy surface.

In [ ]:
# Plot.
x_line=np.linspace(-2.0,2.0,100)
y_line=np.linspace(-2.0,2.0,100)
x,y=np.meshgrid(x_line,y_line)

plt.subplots(1, figsize=(30,15))
plt.pcolor(x,y,np.exp(-f.U(x,y,function)),cmap='Greys')
plt.colorbar()
plt.contour(x,y,np.exp(-f.U(x,y,function)),colors='k',alpha=0.5)
plt.xlabel('$m_1$')
plt.ylabel('$m_2$')
plt.title('potential energy',pad=20)
plt.show()

## 3. Cholesky decomposition of inverse mass matrix

To draw momentum vectors $\mathbf{p}$ from a Gaussian with covariance $\mathbf{M}$, we need the Cholesky decomposition $\mathbf{M}^{-1} = \mathbf{L} \mathbf{L}^T$ of the mass matrix inverse. We pre-compute this decomposition here. $$ $$

In [ ]:
LT=np.linalg.cholesky(Minv).transpose()
LTinv=np.linalg.inv(LT)

## 4. Leapfrog integrator

For clarity, we define the leap-frog integrator as a separate function.

In [ ]:
def leapfrog(m,p,Nt,dt,Minv,plot=False):
    """ Leapfrog integration of Hamilton's equations.
    
    :param m: Initial model (position).
    :param p: Initial momentum.
    :param Nt: Number of leapfrog time steps.
    :param dt: Integration time step.
    :param Minv: Inverse mass matrix.
    :param plot: Plot trajecotry. Only do this for small number of samples.
    
    Return final model (position) and momentum.
    """
    
    # Plot potential energy in the background.
    if plot: 
        plt.subplots(1, figsize=(30,15))
        plt.pcolor(x,y,np.exp(-f.U(x,y,function)),cmap='binary')
        plt.contour(x,y,np.exp(-f.U(x,y,function)),colors='k',alpha=0.5)
        plt.plot(m[0],m[1],'bo',MarkerSize=15)
        
    H=np.zeros(Nt)
    J=f.J(m[0],m[1],function)
    
    # Loop through time steps.
    for k in range(np.int(Nt*np.random.rand())):
    #for k in range(Nt):
        
        # Save previous one for plotting.
        if plot: m_old=m.copy()
        
        # Actual leapfrog step.
        p=p-0.5*dt*J
        m=m+dt*Minv.dot(p)
        J=f.J(m[0],m[1],function)
        p=p-0.5*dt*J
        
        # Compute energy for monitoring.
        H[k]=f.U(m[0],m[1],function)+0.5*np.dot(p,p)
        
        # Plot the trajectory.
        if plot: 
            plt.plot([m_old[0],m[0]],[m_old[1],m[1]],'r')
            plt.plot(m[0],m[1],'kx')
                
    return m, p, H

## 4. Run HMC

We choose a random initial model and then run the standard HMC sampler.

In [ ]:
# Initialisation. =============================================================

# Initialise sample vectors and number of accepted models.
H_trajectory=np.zeros((N,Nit))
m=np.zeros((2,N))
accept=0

# Randomly chosen initial model.
m[:,0]=2.0*(np.random.rand(1,2)-0.5)

# Sampling. ===================================================================

for it in range(N-1):
    
    # Randomly choose momentum.
    p=np.random.randn(2)
    p=LTinv.dot(p)
    
    # Evaluate energies.
    U=f.U(m[0,it],m[1,it],function)
    K=0.5*np.dot(p,np.dot(Minv,p))
    H=U+K
    
    # Run leapfrog iteration.
    m_new,p_new,H_trajectory[it,:]=leapfrog(m[:,it],p,Nit,dt,Minv,plot=plot_trajectories)
    
    # Evaluate new energies.
    U_new=f.U(m_new[0],m_new[1],function)
    K_new=0.5*np.dot(p_new,Minv.dot(p_new))
    H_new=U_new+K_new
    
    # Evaluate Metropolis rule in logarithmic form.
    alpha=np.minimum(0.0,H-H_new)
    if alpha>=np.log(np.random.rand(1)):
        m[:,it+1]=m_new
        accept+=1
    else:
        m[:,it+1]=m[:,it]
        
    # Plot Hamiltonian trajectories.
    if plot_trajectories: 
            plt.xlabel(r'$m_1$')
            plt.ylabel(r'$m_2$')
            plt.show()

## 5. Analyse results

In [ ]:
# Accepted models.
print('%i of %i proposals accepted (%0.2f percent)' % (accept,N,100.0*np.float(accept)/np.float(N)))

# Energy evolution along trajectories.
if plot_trajectories:
    
    t=np.linspace(0.0,np.float(Nit)*dt,Nit)
    
    plt.subplots(1, figsize=(30,15))
    for i in range(N):
        plt.plot(t,H_trajectory[i,:],'k',LineWidth=2)
        plt.plot(t,H_trajectory[i,:],'bo',MarkerSize=12)
        plt.title('H along trajectories',pad=20)
    
    plt.subplots(1, figsize=(30,15))
    for i in range(N):
        plt.plot(t[1:],np.diff(H_trajectory[i,:])/dt,'k',LineWidth=2)
        plt.plot(t[1:],np.diff(H_trajectory[i,:])/dt,'bo',MarkerSize=12)
        plt.title('dH/dt along trajectories',pad=20)

# Posterior histogram.
plt.subplots(1, figsize=(30,15))
plt.hist2d(m[0,:],m[1,:],cmap='binary')
plt.xlabel('$m_1$')
plt.ylabel('$m_2$')
plt.xlim([x_line[0],x_line[-1]])
plt.ylim([y_line[0],y_line[-1]])
plt.colorbar()
plt.title('posterior 2D histogram',pad=20)
plt.show()

In [ ]:
# Trace plots.
plt.subplots(1, figsize=(30,15))
plt.plot(m[0,:],'k',linewidth=4)
plt.plot(m[1,:],'r',linewidth=4)
plt.title('trace plots (black=parameter 1, red=parameter 2)',pad=20)
plt.xlabel('sample index')
plt.ylabel(r'$m_1$, $m_2$')
plt.grid()
plt.show()

# Simple statistics.
mean1=np.mean(m[0,:])
stdv1=np.std(m[0,:])
mean2=np.mean(m[1,:])
stdv2=np.std(m[1,:])
print('means: (%f,%f)' % (mean1,mean2))
print('standard deviations: (%f,%f)' % (stdv1,stdv2))

# Correlations.
cc1=np.correlate(m[0]-mean1,m[0]-mean1,'full')[N-1:2*N]
cc2=np.correlate(m[1]-mean2,m[1]-mean2,'full')[N-1:2*N]
cc1=cc1/np.max(np.abs(cc1))
cc2=cc2/np.max(np.abs(cc2))

# Find index where successive values are below zero.
N1=1
while (N1<N and (cc1[N1-1]>0 or cc1[N1]>0)): N1+=1
N2=1
while (N2<N and (cc2[N2-1]>0 or cc2[N2]>0)): N2+=1
Nmax=np.max((N1,N2))
    
plt.subplots(1, figsize=(30,15))
plt.plot(cc1[0:np.min((2*Nmax,N))],'k',linewidth=4)
plt.plot(cc2[0:np.min((2*Nmax,N))],'r',linewidth=4)
plt.title('intra-parameter correlations (black=parameter 1, red=parameter 2)',pad=20)
plt.xlabel('sample index')
plt.ylabel(r'$cc(m_1)$, $cc(m_2)$')
plt.grid()
plt.show()

# Effective sample size coefficient.
N_max=50
n_eff1=1.0/(1.0+2.0*np.sum(cc1[0:N1]))
n_eff2=1.0/(1.0+2.0*np.sum(cc2[0:N2]))
print('effective sample fractions: (%f,%f)' % (n_eff1,n_eff2))